### Movie Reviews Sentiment Analysis

Kaixin Wang

Spring 2020

In this research project, the goal is to conduct sentiment analysis on a set of movie reviews documents that are collected by Stanford University (Maas et al., 2011). 

The corpus contains a set of training documents and testing documents, and the outcome is whether a piece of movie reivew is positive (`pos`) or negative (`neg`). The corpus is available at  http://ai.stanford.edu/~amaas/data/sentiment/.

- There are 20268 documents in the training set, where 7768 (38.3%) are tagged as `pos` and 12500 (61.7%) are `neg`. 
- There are 20001 documents in the testing  set, where 7501 (37.5%) are tagged as `pos` and 12500 (62.5%) are `neg`. 

To conduct sentiment analysis, we will mainly be using methods from the `nltk` library in Python, which stands for Natural-Language Tool-Kit.

The overall structure of this Natural Language Processing (NLP) project is shown in the following flowchart:
![Flowchart of Moview Reviews Classification](flowchart.png)

Code based on and adapted from the book *Applied Text Analysis with Python* (Bengfort et al., 2018)

# Part I: Corpus Preprocessing

Import basic libraries

In [1]:
import nltk
import numpy as np
import warnings
warnings.filterwarnings("ignore")  # hide the warning messages

In [2]:
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score

In [3]:
import seaborn as sns
import matplotlib.pyplot as plt

Read in the corpus by using `CategorizedPlaintextCorpusReader`: training set

In [4]:
from nltk.corpus.reader.plaintext import CategorizedPlaintextCorpusReader

DOC_PATTERN = r'(?!\.)[\w_\s]+/\d+_\d.txt'    # format of each txt file name
CAT_PATTERN = r'([\w_\s]+)/.*'                # format of the name of each category

corpus = CategorizedPlaintextCorpusReader(
    './aclImdb/train', DOC_PATTERN, cat_pattern = CAT_PATTERN
)

Check the `fileid` of each document in the corpus

In [5]:
corpus.fileids()[0:10] # fileid of the first 10 documents in the corpus

['neg/0_3.txt',
 'neg/10000_4.txt',
 'neg/10001_4.txt',
 'neg/10002_1.txt',
 'neg/10003_1.txt',
 'neg/10004_3.txt',
 'neg/10005_3.txt',
 'neg/10006_4.txt',
 'neg/10007_1.txt',
 'neg/10008_2.txt']

Check the `category` of each document in the corpus

In [6]:
corpus.categories() # types of labels

['neg', 'pos']

Check the total number of documents in the corpus

In [7]:
len(corpus.fileids()) # number of documents in the corpus

20268

Import the `TextNormalizer` class that performs:

- text normalization
- text lemmetization

In [8]:
import unicodedata
from sklearn.base import BaseEstimator, TransformerMixin
nltk.download("stopwords")
nltk.download("wordnet")
from nltk.stem import WordNetLemmatizer
from nltk.corpus import wordnet as wn
class TextNormalizer(BaseEstimator, TransformerMixin):

    def __init__(self, language='english'):
        self.stopwords  = set(nltk.corpus.stopwords.words(language))
        self.lemmatizer = WordNetLemmatizer()

    def is_punct(self, token):
        return all(
            unicodedata.category(char).startswith('P') for char in token
        )

    def is_stopword(self, token):
        return token.lower() in self.stopwords
    
    def normalize(self, document):
        return [
            self.lemmatize(token, tag).lower()
            for paragraph in document
            for sentence in paragraph
            for (token, tag) in sentence
            if not self.is_punct(token) and not self.is_stopword(token)
        ]
    
    def lemmatize(self, token, pos_tag):
        tag = {
            'N': wn.NOUN,
            'V': wn.VERB,
            'R': wn.ADV,
            'J': wn.ADJ
        }.get(pos_tag[0], wn.NOUN)

        return self.lemmatizer.lemmatize(token, tag)
    
    def fit(self, X, y=None):
        return self

    def transform(self, documents):
        for document in documents:
            yield self.normalize(document)

[nltk_data] Downloading package stopwords to C:\Users\Wang
[nltk_data]     Kaixin\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to C:\Users\Wang
[nltk_data]     Kaixin\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [9]:
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\Wang Kaixin\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [10]:
nltk.download("punkt")

[nltk_data] Downloading package punkt to C:\Users\Wang
[nltk_data]     Kaixin\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

Define the `tokenize` function: 

In [11]:
def tokenize(text):
    '''
    Input a list of words, turn the word into lowercaes if the word 
    does not have any punctuation marks, is not a stopword, and is not
    equivalent to the string "br" (a tag parsed from HTML pages).
    Output the list of words filtered (all lowercases).
    '''
    normalizer = TextNormalizer()
    stem = nltk.stem.SnowballStemmer('english')
    return [token.lower() for token in text if len(set(token).intersection(string.punctuation)) == 0 
           and not normalizer.is_stopword(token) and token != "br"]

In [12]:
from nltk import pos_tag, sent_tokenize, wordpunct_tokenize
import string

def postag(corpus):
    '''
    Input a corpus and add the part-of-speech (POS) tagging to each word.
    Output a list of list of list of tuples in the form of (word, POS).
    '''
    return [
        [[pos_tag(tokenize(sent)) for sent in paragraph] 
         for paragraph in corpus.paras(fileids = id)] 
        for id in corpus.fileids()
    ]

Import the `CorpusLoader` class: create the label of each document based on its category

In [13]:
from sklearn.model_selection import KFold

class CorpusLoader(object):

    def __init__(self, reader, folds=12, shuffle=True, categories=None):
        self.reader = reader
        self.folds  = KFold(n_splits=folds, shuffle=shuffle)
        self.files  = np.asarray(self.reader.fileids(categories=categories))
        
    def fileids(self, idx=None):
        if idx is None:
            return self.files
        return self.files[idx]

    def documents(self, idx=None):
        for fileid in self.fileids(idx):
            yield list(self.reader.docs(fileids=[fileid]))

    def labels(self, idx=None):
        return [
            self.reader.categories(fileids=[fileid])[0]
            for fileid in self.fileids(idx)
        ]
        
    def __iter__(self):
        for train_index, test_index in self.folds.split(self.files):
            X_train = self.documents(train_index)
            y_train = self.labels(train_index)

            X_test = (self.documents(test_index))
            y_test = self.labels(test_index)

            yield X_train, X_test, y_train, y_test

Create the training set `X` and `y` based on the training corpus

In [14]:
X_train = postag(corpus)
y_train = CorpusLoader(corpus).labels()

Import the testing set using `CategorizedPlaintextCorpusReader`

In [15]:
from nltk.corpus.reader.plaintext import CategorizedPlaintextCorpusReader

DOC_PATTERN = r'(?!\.)[\w_\s]+/\d+_\d.txt'
CAT_PATTERN = r'([\w_\s]+)/.*'

corpus_test = CategorizedPlaintextCorpusReader(
    './aclImdb/test', DOC_PATTERN, cat_pattern=CAT_PATTERN
)

Create the testing set `X` and `y` based on the training corpus

In [16]:
X_test = postag(corpus_test)
y_test = CorpusLoader(corpus_test).labels()

Statistics of `pos` and `neg` documents in the corpus

In [17]:
import pandas as pd

In [18]:
pd.Series(y_train).value_counts()

neg    12500
pos     7768
dtype: int64

In [19]:
pd.Series(y_train).value_counts() / len(y_train) # proportion of each category in the training set

neg    0.616736
pos    0.383264
dtype: float64

In [20]:
pd.Series(y_test).value_counts()

neg    12500
pos     7501
dtype: int64

In [21]:
pd.Series(y_test).value_counts() / len(y_test)  # proportion of each category in the testing set

neg    0.624969
pos    0.375031
dtype: float64

# Part II: Graphical visualization

To visualize the frequency distribution of the words in the training set and the testing set, we will follow the following steps:

![frequencyDist](words.png)

Define the function `getDocument`: recombine the list of list of list of words into sentences (the reverse of `corpus.paras()`)

In [22]:
def getDocument(corpus):
    docs = [[[" ".join(tokenize(sent)) for sent in paragraph] 
              for paragraph in corpus.paras(fileids = id)] 
             for id in corpus.fileids()]
    documents = []
    for doc in docs:
        content = []
        for paragraph in doc:
            for sentence in paragraph:
                content.append(sentence)
        documents.append(content)
    docs = [" ".join(document) for document in documents]
    return docs

Import `FreqDistVisualizer` and `CountVectorizer`

In [23]:
from yellowbrick.text.freqdist import FreqDistVisualizer
from sklearn.feature_extraction.text import CountVectorizer

Create the documents to visualize the frequency distribution of words

In [24]:
from sklearn.feature_extraction.text import TfidfVectorizer
doc_train = getDocument(corpus)
doc_test  = getDocument(corpus_test)

Plot the frequency distribution of words in the training set

In [25]:
plt.figure(figsize = (14,10), dpi = 1000)
vectorizer = CountVectorizer(stop_words='english')
docs = vectorizer.fit_transform(doc_train)
features = vectorizer.get_feature_names()
visualizer = FreqDistVisualizer(features=features)
visualizer.fit(docs)
visualizer.poof()

Plot the frequency distribution of the words in the testing set

In [26]:
plt.figure(figsize = (14,10), dpi = 1000)
vectorizer = CountVectorizer(stop_words='english')
docs = vectorizer.fit_transform(doc_test)
features = vectorizer.get_feature_names()
visualizer = FreqDistVisualizer(features=features)
visualizer.fit(docs)
visualizer.poof()

# Part III: Classification Methods

Define the `create_pipeline` function: create a `Pipeline` of classifiers

In [27]:
from sklearn.pipeline import Pipeline
from sklearn.decomposition import TruncatedSVD
from sklearn.feature_extraction.text import TfidfVectorizer

def identity(words):
    return words

def create_pipeline(estimator, reduction=False):

    steps = [
        ('normalize', TextNormalizer()),
        ('vectorize', TfidfVectorizer(
            tokenizer=identity, preprocessor=None, lowercase=False
        ))
    ]

    if reduction:
        steps.append((
            'reduction', TruncatedSVD(n_components=1000)
        ))

    # Add the estimator
    steps.append(('classifier', estimator))
    return Pipeline(steps)

Create the classifiers: `LogisticRegression` and `SGDClassifier`

Note that: `SGDClassifier` is a collection of linear classifiers (SVM, logistic regression, a.o.) with SGD training.

This estimator implements regularized linear models with stochastic gradient descent (SGD) learning: the gradient of the loss is estimated each sample at a time and the model is updated along the way with a decreasing strength schedule (aka learning rate). By default, it fits a `linear support vector machine (SVM)`.

The classification pipeline that we will build using logistic regression and support vector machine is shown below:

![classifiers](classifiers.png)

In [28]:
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import MultinomialNB
from sklearn.linear_model import SGDClassifier
import xgboost as xgb

models = []
for form in (LogisticRegression, SGDClassifier):
    models.append(create_pipeline(form(), True))
    
for model in models:
    model.fit(X_train, y_train)

Evaluate the classification accuracy of the training set

In [29]:
scores = []
preds_train  = []
for model in models:
    y_pred = model.predict(X_train)
    scores.append(sum(y_pred == y_train) / len(y_train))
    preds_train.append(y_pred)
print(scores)

[0.8896289717781725, 0.8923919478981646]


From the outputs, the classification accuracy on the training set is 88.96% by using `LogisticRegression` and 89.24% by using `SGDClassifier`.

Evaluate the classification accuracy of the testing set

In [30]:
scores = []
preds_test  = []
for model in models:
    y_pred = model.predict(X_test)
    scores.append(sum(y_pred == y_test) / len(y_test))
    preds_test.append(y_pred)
print(scores)

[0.8647067646617669, 0.8694065296735163]


From the outputs, the classification accuracy on the training set is 86.47% by using `LogisticRegression` and 89.94% by using `SGDClassifier`.

Confusion matrix of using `LogisticRegression` classifier

In [31]:
plt.figure(figsize = (14,5), dpi = 1000)
plt.subplot(1,2,1)
cm = confusion_matrix(y_train, preds_train[0])
sns.heatmap(cm, annot = True, fmt='g')
plt.title("Training set")
plt.xlabel("Predicted")
plt.ylabel("True")
plt.subplot(1,2,2)
cm = confusion_matrix(y_test, preds_test[0])
sns.heatmap(cm, annot = True, fmt='g')
plt.title("Testing set")
plt.xlabel("Predicted")
plt.ylabel("True")
plt.suptitle("LogisticRegression Confusion Matrix")
plt.show()

Confusion matrix of using `SGDClassifier` classifier

In [32]:
plt.figure(figsize = (14,5), dpi = 1000)
plt.subplot(1,2,1)
cm = confusion_matrix(y_train, preds_train[1])
sns.heatmap(cm, annot = True, fmt='g')
plt.title("Training set")
plt.xlabel("Predicted")
plt.ylabel("True")
plt.subplot(1,2,2)
cm = confusion_matrix(y_test, preds_test[1])
sns.heatmap(cm, annot = True, fmt='g')
plt.title("Testing set")
plt.xlabel("Predicted")
plt.ylabel("True")
plt.suptitle("SGDClassifier Confusion Matrix")
plt.show()

# Part IV: Deep Learning Method - Neural Network

The neural network pipeline that we will build is shown below:

![kerasClassifier](keras.png)

Build `KerasClassifier` model (Neural Network)

In [33]:
import tensorflow as tf

In [34]:
from keras.layers import Dense
from keras.models import Sequential


N_FEATURES = 5000
N_CLASSES = 2

def build_network():
    """
    Create a function that returns a compiled neural network
    """
    nn = Sequential()
    nn.add(Dense(500, activation='relu', input_shape=(N_FEATURES,)))
    nn.add(Dense(150, activation='relu'))
    nn.add(Dense(N_CLASSES, activation='softmax'))
    nn.compile(
        loss='categorical_crossentropy',
        optimizer='adam',
        metrics=['accuracy']
    )
    return nn

Using TensorFlow backend.


In [35]:
from keras.wrappers.scikit_learn import KerasClassifier

In [36]:
# modified version of train_model from the book
from sklearn.model_selection import cross_val_score

def train_model(X_train, y_train, X_test, y_test, model):
    """
    Trains model from corpus; constructing cross-validation
    scores using the cv parameter, then fitting the model on the full data.
    Returns the scores.
    """
    
    # Fit the model on entire dataset
    model.fit(X_train, y_train)
    scores = model.score(X_test, y_test)
    preds_train  = model.predict(X_train)
    preds_test  = model.predict(X_test)

    # Return scores and predictions
    return (scores, preds_train, preds_test)

Normalize the input features by using the `normalize` function in `TextNormalizer` 

In [37]:
normalizer = TextNormalizer()
train_X = [normalizer.normalize(X_train[i]) for i in range(len(X_train))]
X_training = [" ".join(doc) for doc in train_X]
test_X = [normalizer.normalize(X_test[i]) for i in range(len(X_test))]
X_testing = [" ".join(doc) for doc in test_X]

Build a `KerasClassifier` pipeline that transforms the input by `TextNormalizer` and `TfidfVectorizer`

In [38]:
from sklearn.pipeline import Pipeline
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.feature_extraction.text import TfidfVectorizer

pipeline = Pipeline([
    # ('norm', TextNormalizer()),   # have normalized the text in the previous code chunk
    ('vect', TfidfVectorizer(max_features=N_FEATURES)),
    ('nn', KerasClassifier(build_fn=build_network,
                           epochs=30, batch_size=128))
])

In [39]:
scores_keras, kpred_train, kpred_test = train_model(X_training, y_train, X_testing, y_test, pipeline)

Epoch 1/30
20268/20268 [==============================] - 20s 1ms/step - loss: 0.3691 - accuracy: 0.8260
Epoch 2/30
20268/20268 [==============================] - 13s 659us/step - loss: 0.2011 - accuracy: 0.9228
Epoch 3/30
20268/20268 [==============================] - 13s 650us/step - loss: 0.0917 - accuracy: 0.9704
Epoch 4/30
20268/20268 [==============================] - 13s 646us/step - loss: 0.0152 - accuracy: 0.9968
Epoch 5/30
20268/20268 [==============================] - 13s 662us/step - loss: 0.0028 - accuracy: 0.9996
Epoch 6/30
20268/20268 [==============================] - 14s 667us/step - loss: 4.9126e-04 - accuracy: 1.0000
Epoch 7/30
20268/20268 [==============================] - 14s 682us/step - loss: 2.6301e-04 - accuracy: 1.0000
Epoch 8/30
20268/20268 [==============================] - 14s 676us/step - loss: 1.7067e-04 - accuracy: 1.0000
Epoch 9/30
20268/20268 [==============================] - 14s 681us/step - loss: 1.0339e-04 - accuracy: 1.0000
Epoch 10/30
20268/20268

In [40]:
print(scores_keras)

0.8428078889846802


From the output above, the classification accuracy on the testing set is 84.28% by using `KerasClassifier` with `TextNormalizer`.

Confusion matrix of using `KerasClassifier` classifier with `TextNormalizer`

In [41]:
plt.figure(figsize = (14,5), dpi = 1000)
plt.subplot(1,2,1)
cm_keras = confusion_matrix(y_train, kpred_train)
sns.heatmap(cm_keras, annot = True, fmt='g')
plt.title("Training set")
plt.xlabel("Predicted")
plt.ylabel("True")
plt.subplot(1,2,2)
cm_keras = confusion_matrix(y_test, kpred_test)
sns.heatmap(cm_keras, annot = True, fmt='g')
plt.title("Testing set")
plt.xlabel("Predicted")
plt.ylabel("True")
plt.suptitle("KerasClassifier (TextNormalizer) Confusion Matrix")
plt.show()

Extract the keyphrases in the input features by defining the `KeyphraseExtractor` class

In [42]:
from keras.preprocessing import sequence
from nltk import RegexpParser
from unicodedata import category as unicat
from itertools import groupby
from nltk.chunk import tree2conlltags

In [43]:
class KeyphraseExtractor(BaseEstimator, TransformerMixin):
    """
    Extract adverbial and adjective phrases, and transform
    documents into lists of these keyphrases, with a total
    keyphrase lexicon limited by the nfeatures parameter
    and a document length limited/padded to doclen
    """
    def __init__(self, nfeatures=100000, doclen=60):
        self.grammar = r'KT: {(<RB.> <JJ.*>|<VB.*>|<RB.*>)|(<JJ> <NN.*>)}'
        self.chunker = RegexpParser(self.grammar)
        self.nfeatures = nfeatures
        self.doclen = doclen
        
    def normalize(self, sent):
        is_punct = lambda word: all(unicat(c).startswith('P') for c in word)
        sent = filter(lambda t: not is_punct(t[0]), sent)
        sent = map(lambda t: (t[0].lower(), t[1]), sent)
        return list(sent)

    def extract_candidate_phrases(self, sents):
        """
        For a document, parse sentences using our chunker created by
        our grammar, converting the parse tree into a tagged sequence.
        Extract phrases, rejoin with a space, and yield the document
        represented as a list of its keyphrases.
        """
        for sent in sents:
            sent = self.normalize(sent)
            if not sent: continue
            chunks = tree2conlltags(self.chunker.parse(sent))
            phrases = [
                " ".join(word for word, pos, chunk in group).lower()
                for key, group in groupby(
                    chunks, lambda term: term[-1] != 'O'
                ) if key
            ]
            for phrase in phrases:
                yield phrase
                
    def get_lexicon(self, keydocs):
        """
        Build a lexicon of size nfeatures
        """
        keyphrases = [keyphrase for doc in keydocs for keyphrase in doc]
        fdist = FreqDist(keyphrases)
        counts = fdist.most_common(self.nfeatures)
        lexicon = [phrase for phrase, count in counts]
        return {phrase: idx+1 for idx, phrase in enumerate(lexicon)}

    def clip(self, keydoc, lexicon):
        """
        Remove keyphrases from documents that aren't in the lexicon
        """
        return [lexicon[keyphrase] for keyphrase in keydoc
                if keyphrase in lexicon.keys()]
    
    def fit(self, documents, y=None):
        return self

    def transform(self, documents):
        docs = [list(self.extract_candidate_phrases(doc)) for doc in documents]
        lexicon = self.get_lexicon(docs)
        clipped = [list(self.clip(doc, lexicon)) for doc in docs]
        return sequence.pad_sequences(clipped, maxlen=self.doclen)

Extract the keyphrases by using the `extract_candidate_phrases` function in `KeyphraseExtractor` class

In [44]:
extractor = KeyphraseExtractor()
key_train = [[list(extractor.extract_candidate_phrases(sent)) for sent in X_train[i]]
             for i in range(len(X_train))]
key_test = [[list(extractor.extract_candidate_phrases(sent)) for sent in X_test[i]]
             for i in range(len(X_test))]
k_train = [["   ".join(sent) for sent in key_train[i]]
           for i in range(len(key_train))]
k_test = [["   ".join(sent) for sent in key_test[i]]
           for i in range(len(key_test))]
k_train = [doc[0] for doc in k_train]
k_test = [doc[0] for doc in k_test]

Build a `KerasClassifier` pipeline that transforms the input by `KeyphraseExtractor` and `TfidfVectorizer`

In [45]:
from sklearn.pipeline import Pipeline
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.feature_extraction.text import TfidfVectorizer

pipeline = Pipeline([
    # ('keyphrase', KeyphraseExtractor()), # have extracted the keyphrases in the previous code chunk
    ('vect', TfidfVectorizer(max_features=N_FEATURES)),
    ('nn', KerasClassifier(build_fn=build_network,
                           epochs=20))
])

In [46]:
scores_keras, kpred_train, kpred_test = train_model(k_train, y_train, k_test, y_test, pipeline)

Epoch 1/20
20268/20268 [==============================] - 46s 2ms/step - loss: 0.3984 - accuracy: 0.8157
Epoch 2/20
20268/20268 [==============================] - 46s 2ms/step - loss: 0.2302 - accuracy: 0.9069
Epoch 3/20
20268/20268 [==============================] - 46s 2ms/step - loss: 0.0636 - accuracy: 0.9787
Epoch 4/20
20268/20268 [==============================] - 48s 2ms/step - loss: 0.0063 - accuracy: 0.9984
Epoch 5/20
20268/20268 [==============================] - 47s 2ms/step - loss: 9.8228e-04 - accuracy: 0.9999
Epoch 6/20
20268/20268 [==============================] - 47s 2ms/step - loss: 2.0295e-04 - accuracy: 0.9999
Epoch 7/20
20268/20268 [==============================] - 47s 2ms/step - loss: 8.9485e-05 - accuracy: 1.0000
Epoch 8/20
20268/20268 [==============================] - 47s 2ms/step - loss: 5.4641e-05 - accuracy: 1.0000
Epoch 9/20
20268/20268 [==============================] - 47s 2ms/step - loss: 3.2515e-05 - accuracy: 1.0000
Epoch 10/20
20268/20268 [==========

In [47]:
print(scores_keras) 

0.817509114742279


From the output above, the classification accuracy on the testing set is 81.75% by using `KerasClassifier` with `KeyPhraseExtractor`.

Confusion matrix of using `KerasClassifier` classifier with `KeyphraseExtractor`

In [48]:
plt.figure(figsize = (14,5), dpi = 1000)
plt.subplot(1,2,1)
cm_keras = confusion_matrix(y_train, kpred_train)
sns.heatmap(cm_keras, annot = True, fmt='g')
plt.title("Training set")
plt.xlabel("Predicted")
plt.ylabel("True")
plt.subplot(1,2,2)
cm_keras = confusion_matrix(y_test, kpred_test)
sns.heatmap(cm_keras, annot = True, fmt='g')
plt.title("Testing set")
plt.xlabel("Predicted")
plt.ylabel("True")
plt.suptitle("KerasClassifier (KeyphraseExtractor) Confusion Matrix")
plt.show()

# Part V: Analysis

Based on the classifiers that we built above:

Classifier | Losigtic Regression | linear SVM | Keras Classifier (TF-IDF) | Keras Classifier (Keyphrase)
-----------|----------|--------|-------------|-------------
Method | `LogisticRegression` |  `SGDClassifier` | `KerasClassifier` | `KerasClassifier` 
Accuracy | 0.8647 |  0.8694 | 0.8428 | 0.8175 

Comparisons:

- `LogisticRegression`: has a relatively high classification accuracy, but it takes relatively long to fit the model
- `SGDClassifier`: also has a relatively high classification accuracy, and also takes quite a bit to fit the model
- `KerasClassifier`: using this deep learning framework, it takes a small amount of time to the classifier pipelines, although the overall performance on the testing set is not as high; one possible issue is overfitting on the training set

# Part VI: Future Steps

We saw from the analysis that the logistic regression and support vector machine classifiers, which are traditional machine learning methods, had relatively better classification performances than the deep learning neural networks. One possible reason for this is that the ANNs are overfitting the training set. So we can further explore how to balance the trade-offs between model complexity and model generality. 

Another possible improvement is on the speed of executing the entire program. In the current version, the step of transforming the raw text into numeric features so that machine learning can understand takes quite a long time, and the process of building the classification pipelines also takes time. To speed up the computations, we can scale the text analytics through using multiprocessing or Spark, two methods that are frequently used to distribute a large workload to multiple computational resources (e.g., processes, disks, memory).

    Updated by Kaixin Wang, May 2020